###### imports and settings

In [2]:
import osmnx as ox
import geopandas as gpd
import pandas as pd
import requests
import matplotlib.pyplot as plt
import numpy as np
# import networkx as nx
# from descartes import PolygonPatch
# from shapely.geometry import Point, LineString, Polygon
#import sklearn
import folium
from folium import plugins
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
%matplotlib inline
ox.config(log_console=True)
ox.__version__
from warnings import simplefilter
simplefilter(action="ignore", category=pd.errors.PerformanceWarning)
pd.set_option('display.max_rows', 1000); pd.set_option('display.max_columns', 1000); pd.set_option('display.width', 1000)

C:\Users\jmccall\AppData\Local\anaconda3\envs\openstreets\lib\site-packages\osmnx\utils.py:192: UserWarning: The `utils.config` function is deprecated and will be removed in a future release. Instead, use the `settings` module directly to configure a global setting's value. For example, `ox.settings.log_console=True`.
  warnings.warn(


In [3]:
#bring in all rides for a heatmap of dropoffs
rides = pd.read_csv('../data/accessrides.csv')
alldropoffs = rides.loc[rides['Type'] == 'Dropoff'].reset_index(drop = True)
alldropoffs = gpd.GeoDataFrame(alldropoffs, geometry=gpd.points_from_xy(alldropoffs.LONG, alldropoffs.LAT), crs = 'NAD83')

In [4]:
alldropoffs['LAT'] = alldropoffs['LAT'].astype(str)
alldropoffs['LONG'] = alldropoffs['LONG'].astype(str)

In [5]:
#make list with long then lat for folium
locations = alldropoffs[['LONG', 'LAT']]
locationlist = locations.values.tolist()

foliumnewlist = []
for i in locationlist:
  if i not in foliumnewlist:
    foliumnewlist.append(i)

In [6]:
#bring in county boundaries
url = 'https://www2.census.gov/geo/tiger/TIGER2020/COUNTY/tl_2020_us_county.zip'
counties = gpd.read_file(url)
print('Your geographic file is ready.')

Your geographic file is ready.


In [7]:
counties = counties.loc[counties['STATEFP'] == '47']

In [8]:
#get building data from OSMnx
buildings = ox.geometries.geometries_from_point([36.140019, -86.807914], tags = {'building': True}, dist = 30000)

In [9]:
buildings = buildings[['name', 'geometry']]
buildings = buildings.reset_index(drop = True).dropna()

In [10]:
topfive = gpd.read_file('../data/DropOff_Density_Top5P.shp')
topfive = topfive.to_crs(4326)

In [11]:
topten = gpd.read_file('../data/DropOff_Density_Top10P.shp')
topten = topten.to_crs(4326)

In [12]:
toptwentyfive = gpd.read_file('../data/DropOff_Density_Top25P.shp')
toptwentyfive = toptwentyfive.to_crs(4326)

In [13]:
#clip buildings to the top 5 
buildings_top5 = gpd.clip(buildings, topfive).reset_index(drop = True)
buildings_top5.to_crs(4326, inplace = True)
#make a properly formatted coordinate list
coord_list_top5 = [(x,y) for x,y in zip(buildings_top5['geometry'].centroid.x , buildings_top5['geometry'].centroid.y)]

C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\1813999714.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  coord_list_top5 = [(x,y) for x,y in zip(buildings_top5['geometry'].centroid.x , buildings_top5['geometry'].centroid.y)]
C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\1813999714.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  coord_list_top5 = [(x,y) for x,y in zip(buildings_top5['geometry'].centroid.x , buildings_top5['geometry'].centroid.y)]


In [14]:
#clip buildings to the top 10
buildings_top10 = gpd.clip(buildings, topten).reset_index(drop = True)
buildings_top10.to_crs(4326, inplace = True)
#make a properly formatted coordinate list
coord_list_top10 = [(x,y) for x,y in zip(buildings_top10['geometry'].centroid.x , buildings_top10['geometry'].centroid.y)]

C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\1451849817.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  coord_list_top10 = [(x,y) for x,y in zip(buildings_top10['geometry'].centroid.x , buildings_top10['geometry'].centroid.y)]
C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\1451849817.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  coord_list_top10 = [(x,y) for x,y in zip(buildings_top10['geometry'].centroid.x , buildings_top10['geometry'].centroid.y)]


In [15]:
#clip buildings to the top 25
buildings_top25 = gpd.clip(buildings, toptwentyfive).reset_index(drop = True)
buildings_top25.to_crs(4326, inplace = True)
#make a properly formatted coordinate list
coord_list_top25 = [(x,y) for x,y in zip(buildings_top25['geometry'].centroid.x , buildings_top25['geometry'].centroid.y)]

C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\17885246.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  coord_list_top25 = [(x,y) for x,y in zip(buildings_top25['geometry'].centroid.x , buildings_top25['geometry'].centroid.y)]
C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\17885246.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  coord_list_top25 = [(x,y) for x,y in zip(buildings_top25['geometry'].centroid.x , buildings_top25['geometry'].centroid.y)]


In [16]:
buildings['lon'] = buildings.centroid.x 
buildings['lat'] = buildings.centroid.y 
buildings_top5['lon'] = buildings_top5.centroid.x 
buildings_top5['lat'] = buildings_top5.centroid.y 
buildings_top10['lon'] = buildings_top10.centroid.x 
buildings_top10['lat'] = buildings_top10.centroid.y 
buildings_top25['lon'] = buildings_top25.centroid.x 
buildings_top25['lat'] = buildings_top25.centroid.y 

C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\3613153875.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  buildings['lon'] = buildings.centroid.x
C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\3613153875.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  buildings['lat'] = buildings.centroid.y
C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\3613153875.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  buildings_top5['lon'] = buildings_top5.centroid.x
C:\Users\jmccall\AppData\Local\Temp\ipykernel_9960\3613153875.py:4: UserWarning: Geometry is in a geograp

In [17]:
downtown = (36.165142, -86.776157)

In [24]:
map = folium.Map((downtown), zoom_start= 11, tiles = 'CartoDB positron')

#building markers
mc = MarkerCluster(name = 'Building Markers')
for row in buildings_top5.itertuples():
    mc.add_child(folium.Marker(location = [row.lat, row.lon], icon = folium.Icon(color = 'black', icon = 'circle', prefix = 'fa'),
                              popup = 'Building: {}'.format(row.name)))#.format(name = row.name))
 #parameters for heatmap   
heat_data = [[point.xy[1][0], point.xy[0][0]] for point in alldropoffs.geometry]
radius = 19
#heatmap for all dropoffs
heat = plugins.HeatMap(heat_data, name = 'Heatmap', radius = radius, max_zoom = 19, 
                min_opacity = 0.2, blur = 12, overlay = True, control = True, show = True, gradient={0: 'navy', 0.25: 'blue', .5: 'green', 0.75: 'orange', 1: 'red'})
#geojson polygons for the top 5th, 10th, and 25th percentile aggregated hex areas
topfivepoly = folium.GeoJson(data=topfive["geometry"], name = 'Top Fifth Percentile', control = True, show = True)
toptenpoly = folium.GeoJson(data=topten["geometry"], name = 'Top Tenth Percentile', control = True, show = False)
toptwentyfifthpoly = folium.GeoJson(data=toptwentyfive["geometry"], name = 'Top Twenty-Fifth Percentile', control = True, show = False)
#add layers
map.add_child(mc)
map.add_child(heat)
map.add_child(topfivepoly)
map.add_child(toptenpoly)
map.add_child(toptwentyfifthpoly)
#print aggregation radius information
metersinitial = radius * 76.437
metersmax = radius * 0.299
print('Meters in aggregation radius at initial zoom level: ' + str(metersinitial))
print('Meters in aggregation radius at maximum zoom level: ' + str(metersmax))
#enable layer control
folium.LayerControl().add_to(map)
#display map
map

Meters in aggregation radius at initial zoom level: 1452.3029999999999
Meters in aggregation radius at maximum zoom level: 5.681


In [19]:
top5list = pd.DataFrame(buildings_top5.name.unique())

In [20]:
top5list.to_csv('../data/top5thpercentilegeneratedlist.csv')